In [98]:
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.datasets import fetch_20newsgroups
from sklearn.decomposition import NMF, LatentDirichletAllocation
import numpy as np
from collections import OrderedDict

In [2]:
dataset = fetch_20newsgroups(subset='test', remove=('headers', 'footers', 'quotes'))
documents = dataset.data

In [3]:
from elasticsearch import Elasticsearch
es = Elasticsearch([{'host': 'localhost', 'port': 9200}])

In [4]:
no_features = 1000
# LDA can only use raw term counts for LDA because it is a probabilistic graphical model
def get_tf_vector(document):
    try:
        tf_vectorizer = CountVectorizer()
        tf = tf_vectorizer.fit_transform(document)
        tf_feature_names = tf_vectorizer.get_feature_names()
        return tf,tf_feature_names
    except: return [None,None]




In [12]:
def display_topics(model, feature_names, no_top_words):
    for i in range(model.components_.shape[0]):
        print('\nTopic %d:' % (i))
        topic = model.components_[i]
        result = dict()
        new_topic = topic.argsort()[:-no_top_words - 1:-1]
        for j in new_topic:
            result[feature_names[j]] = topic[j] / np.sum(model.components_, axis=0)[j]
            print(feature_names[j], topic[j] / np.sum(model.components_, axis=0)[j])
        es.index(index='topic', doc_type='topic',id=i,body={
            'topic_id': i,
            'top_words': result
            })

In [13]:
###print top 20 words for the topics
i = 0
while i < 3:
    if i == 0:
        no_topics = 10
    elif i == 1:
        no_topics = 20
    elif i == 2:
        no_topics = 50
    tf,tfidf_feature_names = get_tf_vector(documents)
        
    lda = LatentDirichletAllocation(n_topics=no_topics).fit(tf)
    print("------- Top 20 words for all docs for K=",no_topics)
    r = display_topics(lda,tfidf_feature_names,20)
    i+=1

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)


------- Top 20 words for all docs for K= 10

Topic 0:
the 0.20140043753487258
of 0.21244809201719847
and 0.2076836029444818
in 0.23624917232533743
to 0.10119773764898553
he 0.8254330237319973
was 0.4772738967286037
that 0.12132574818997043
his 0.816858437990415
for 0.1198249309949436
they 0.24716159053369996
as 0.1889202681512353
is 0.07404690458133874
who 0.42869086435776804
on 0.1334610171848742
were 0.4239893693750916
god 0.7943385441034444
by 0.1927120935081083
with 0.11780682083074075
had 0.3764882075743488

Topic 1:
the 0.04869479062791654
of 0.08888274612601497
and 0.044914100199310934
in 0.06135531842477017
by 0.13444191352530066
were 0.1571400109196247
armenian 0.9975973903555339
to 0.010832871535240068
armenians 0.9970390161320738
from 0.0551027596618957
their 0.10494086148035475
jews 0.818637961874646
ed 0.7718142160418532
war 0.757201925184682
jewish 0.7180796962725253
university 0.4698650762677127
muslims 0.9956542995455714
muslim 0.9955537201521313
turkish 0.9955238266123

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)


------- Top 20 words for all docs for K= 20

Topic 0:
cosy_pak 0.9698205586051588
s4 0.7739923678508385
av 0.9524878250754849
ge 0.9519872981632008
ke 0.9475797377579659
sm 0.9431522658816909
dw 0.9403888783163096
oo 0.7210422080793842
az 0.7666383167145133
hq 0.6716601191006162
hs 0.5560643445116588
pw 0.8890545943010238
mishna 0.9266760235643013
cosy_pak_09 0.9266709728241732
cosy_notes 0.9266562227316255
________________________________________ 0.9266341525943784
weick 0.9244249901663719
fr 0.2471684815189559
rad 0.8240398482720008
sl 0.8359929618527757

Topic 1:
the 0.03176733546290918
of 0.0666234956578837
and 0.03305271448096648
in 0.041873724467203485
by 0.10594533524403532
were 0.16343055261137868
armenian 0.9974638796512062
armenians 0.9968746255955133
ed 0.7572341652710055
university 0.4728819558669124
from 0.04164686118914846
their 0.08022653294312039
turkish 0.9952751568646407
russian 0.9947586146042573
turkey 0.9941839886259499
000 0.3856197152106495
soviet 0.9700681585085

oracle 0.9484028354395635
argv 0.946529670059098
lut_index 0.9450795195926254
sinclair 0.9438863146844233
awards 0.9437425401648418
gc 0.525409123872224

Topic 17:
the 0.10775420800772964
to 0.1461402565791845
and 0.17776416314846025
for 0.34292592419916473
is 0.15958519729422832
of 0.09219124789712131
in 0.11489869182571234
it 0.14993377565443083
with 0.25738167835576276
or 0.30324735960947263
on 0.22114066653651576
you 0.14675728180044395
can 0.3290791249978973
this 0.1820097360897742
if 0.23180626071389498
have 0.15456513474477457
from 0.2460934669692115
are 0.146818082094018
windows 0.9900936326560099
dos 0.9991101685336375

Topic 18:
jehovah 0.9936630034250727
muslims 0.6617383891198764
kuwait 0.9919839118610351
elohim 0.9914902268170184
war 0.3546349307856405
bosnia 0.9580946494430198
arabs 0.8726147386649361
islam 0.8578317076903047
serbs 0.9888387677756747
muslim 0.41188291515411923
father 0.43978970774826476
bosnian 0.9885300275260849
unto 0.9336385506042285
iran 0.94592658439

...

volt 0.913133071594078
fetus 0.9126865542611091
undefined 0.9126335665381093
ndp 0.9111147745243682
alt 0.06653841808886404
consumers 0.9095531339840051

Topic 17:
bruins 0.9864934495296085
devils 0.9747214976717631
islanders 0.9774657232649057
sc 0.9155867442438997
wings 0.7509726960791335
leafs 0.6332721259548596
bar 0.5026898590326806
le 0.5399247710976303
cbc 0.9477911684324622
korea 0.9450270053480616
8v 0.9437297340887393
gl 0.39019902993704314
qualcomm 0.9318502952723714
tortured 0.9269482403330612
loudly 0.9228178940262359
8l 0.9200893052434107
rabbits 0.918378463375928
tubes 0.9173903417661319
nc 0.3836687583797881
surviving 0.9116312286683385

Topic 18:
adl 0.9930140613506203
bullock 0.986461204431849
gerard 0.985155043153395
05pm 0.948708807685477
gurion 0.9486944781930948
kpc 0.9290434863115433
defamation 0.9202444037147898
suall 0.9015616065729
repentant 0.8650632429886348
aipac 0.8624580097136914
humphries 0.8617718709419047
undercover 0.837192644442672
barsky 0.837101357


Topic 33:
dtr 0.9765437901230399
cts 0.9637078789809875
dsr 0.9620975405498262
neat 0.9618979751734812
rts 0.9604120365806972
ir 0.9595812659762787
dte 0.9565049925813475
porter 0.953374009240317
satanic 0.9460006979289878
clever 0.9228908034577886
closing 0.6190017269461796
vocal 0.8986945582142829
dance 0.8965194859548036
sundays 0.896273576637122
ghostscript 0.3809970820942962
abusers 0.895251798412471
oppressive 0.8943758040025812
hartley 0.8939958689448444
murderous 0.8938852240310918
landlord 0.8912015085003134

Topic 34:
xm 0.9630068935109346
builder 0.9255895483251345
ck 0.9057241433190462
fe 0.8973611261230197
donations 0.8798754570465087
hy 0.8764666506596757
commoninteract 0.8580886541840685
parser 0.8473483112391763
slr 0.8326623058761884
955 0.8319467858721803
eos 0.8285380940789386
afc 0.7815516047806953
42m 0.7760426182399043
statictext 0.7664126883276453
pia 0.7606093769105475
myedit 0.7225142749357816
r3t 0.7201898466093581
w5v 0.7183604460186083
1105 0.70129055055308

PUT http://localhost:9200/topic/topic/36 [status:400 request:0.026s]


meg 0.9909737637524744
motherboard 0.9887189267668668
larson 0.9882102234562099
mbytes 0.9502479151872824
mathematica 0.9791673949863607
turbo 0.5743893632086262
66 0.3460146332716088
486dx2 0.9759811265208749
edu 0.030132329693946438
486 0.35383992780523904
vv 0.9758422851889335
33 0.17645236189662333
ibm 0.12621190136288551
bi 0.8673133413846625
stacker 0.9698684827869333


RequestError: TransportError(400, 'illegal_argument_exception', 'Limit of total fields [1000] in index [topic] has been exceeded')

In [99]:
def store_topics(model, feature_names, no_top_words):
    result_topics = {}
    for topic_idx, topic in enumerate(model.components_):
        print("Topic %d:" % (topic_idx))
        #print(" ".join([feature_names[i]
        #                for i in topic.argsort()[:-no_top_words - 1:-1]]))
        new_topic = topic.argsort()[:-no_top_words - 1:-1]
        for j in new_topic:
            
            result_topics[feature_names[j]] = topic[j] / np.sum(model.components_, axis=0)[j]
            es.index(index='topic', doc_type='topic',id=topic_idx,body={
            'topic_id': topic_idx,
            'top_words': {'word':feature_names[j],
                        'probability':result_topics[feature_names[j]]}
            
            })
            print(feature_names[j], result_topics[feature_names[j]])
            
        return result_topics

In [25]:
# Run LDA
i = 0
while i < 3:
    if i == 0:
        no_topics = 10
    elif i == 1:
        no_topics = 20
    elif i == 2:
        no_topics = 50
    
    for index in range(len(documents)):
        
        tf,tfidf_feature_names = get_tf_vector([documents[index]])
        
        if tf is not None:
                lda = LatentDirichletAllocation(n_topics=no_topics).fit(tf)

                a=lda.transform(tf)
                result = dict()
                
                new_topic=a[0].argsort()[:-5 - 1:-1]
                for i in range(len(new_topic)):
                    result[str(new_topic[i])] = a[0][new_topic[i]]
                
                print("------- Top 20 words for K=",no_topics)
                no_top_words = 20
                #result_topics = get_topics(lda, tf_feature_names, 5)
                
                
                es.index(index='index_20ng', doc_type='20_ng',id=index,body={
                'doc_id': index+1,
                'doc_text': documents[index],
                'doc_topics': result
                })
        else:
                result[str(-1)] = 0.0
                es.index(index='index_20ng', doc_type='20_ng',id=index,body={
                'doc_id': index+1,
                'doc_text': documents[index],
                "doc_topics": result
                })
    i += 1
    

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

...

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

In [16]:
# NMF is able to use tf-idf
tfidf_vectorizer = TfidfVectorizer(stop_words='english')
tfidf = tfidf_vectorizer.fit_transform(documents)
tfidf_feature_names = tfidf_vectorizer.get_feature_names()

In [17]:
# Run NMF
i = 0
while i < 3:
    if i == 0:
        no_topics = 10
    elif i == 1:
        no_topics = 20
    elif i == 2:
        no_topics = 50
    
    nmf = NMF(n_components=no_topics).fit(tfidf)
    print("------- NMF Top 20 words for K=",no_topics)
    no_top_words = 20
    display_topics(nmf, tf_feature_names, no_top_words)
    i += 1
    

------- NMF Top 20 words for K= 10
Topic 0:
dogmas 0.9025672173531692
judaic 0.8856693921281661
liberty 0.6960123271813042
th 0.7509578849553111
kku 0.46818515700250607
godhead 0.5916926438432724
valuing 0.6870231191702719
thrace 0.5145570948027207
peacibly 0.33463827128785895
cape 0.9916037801135599
rchori 0.7386000942340409
w7zgyke 0.571664433004336
sandia 0.5032100576062157
gnarly 0.6895407331517273
rfds 0.5245244787334367
tgraf 0.6797620624293272
littered 0.6247617151839943
magnetics 0.47192271792784796
waiver 0.43960806565323834
tgl 0.7678837108459634
Topic 1:
whiles 1.0
fidk 0.9627720217285075
done 0.8552012095786983
whic 1.0
fierpower 0.9361239295632068
printhead 0.7506201286343054
uorp 0.3441916833241151
upadhyay 0.4765191514639009
rs 0.7702549310645973
vd4w 0.6973133007938045
pretext 0.36628022676094396
seminar 0.9014814803298739
mqveio 0.9474343694043053
appetites 0.8665428344805367
rri 0.5084921167650873
schnitzius 0.6535788541259369
frontier 0.542126756913348
pasttime 0.393

adv21 0.8761245039599894
heut 0.6416832717974007
loby 0.4765468231075775
addon 0.7172425361986535
inequities 0.5889752826784798
ellipse 0.43821451088834634
securely 0.40346230980311915
polytechnique 0.3955752373197921
inevitable 0.27928481176781456
limrlk8 0.36167785484459974
appointees 0.45101575768693397
hedaka 0.23382868785772712
insulators 0.28544901208224716
appointee 0.5861479668860191
remembre 0.43144310075946957
madera 0.6946562327264758
antonio 0.2270754562284272
wiretapped 0.4440498344713416
Topic 8:
00 1.0
s9xvsm 0.7992076051632432
10 0.5630926499381976
50 0.7095394769556964
shar_eof 0.7598956007867922
20 0.5551041052173022
nesbitt 0.24605014750495444
premepted 0.4580172208643374
15 0.5950232234487856
occur 0.6200788019819533
25 0.5436035274740653
concidered 0.6125501043984325
30 0.4500170805821003
11 0.5462941277837381
12 0.463882286071434
ashmf4 0.5746762289039788
40 0.516684335082827
insulators 0.33756795345793483
ed78 0.13982042093194058
13 0.5298319156703399
Topic 9:
ca

algiorithm 0.4007379037681758
rushing 0.9413892179433371
scsi2 0.5313789624874766
rotary 0.6048770707390685
menaf00 0.24486443275331227
personal 0.5115473173207608
chig 0.2809910163049948
Topic 5:
drawn 0.9829630788563404
discusing 0.429158963896463
handicapped 0.39033036169037805
dread 0.7385930915038322
flemming 0.5788417390453178
icbm 0.2092604040875548
boobtists 0.628111181121007
contraband 0.1735875270067128
cbtree 0.21099870749225386
hausmann 0.29092233688114055
c9l 0.19215544045366026
intend 0.19394143445143772
survive 0.29318777646140004
compress_exposure 0.11715789524640684
pork 0.09205118276990672
ro3129a 0.28444529193774115
qrpuq 0.5658252153891641
tab 0.20269395447727684
bing 0.2855948015923991
explorers 0.18913120712805262
Topic 6:
godhead 0.9985694433523788
lqs4uo 0.9481290730176242
backplane 0.3343991386432085
preference 0.28467878641128386
bombs 0.18097910051458185
tgl 0.17665457342547045
berthing 0.15977784569162254
qqxl 0.37118880344322075
thrace 0.08204239842596736
p

lingers 0.07094970022429294
littered 0.06034408239935458
biosym 0.04243097341294533
rbrand 0.06559197459132493
cultivated 0.31364991036822626
lin 0.3870462188494319
mathematisches 0.07511087590498405
gsidler 0.09104270586490334
tcm 0.051363503843570225
Topic 22:
snai 0.7848497337521763
gracida 0.9185319984668336
coast 0.557441750965465
committment 0.7039245787265307
ijx 0.5424114962841924
pasttime 0.2658410742653057
p33nd 0.4906239579678034
autosomal 0.28158946701404913
hangeth 0.33868655738622006
compress_exposure 0.2865291080204265
mop7 0.33426676578019787
3d 0.7033549161697457
inevitable 0.21316660777901744
undiscriminating 0.45324889370000976
i8pmc9 0.2654766611236301
darius_lecointe 0.16053752793813383
lgutlgutnl 0.540652554629249
amerikan 0.5494882270051403
solar 0.2389880582357496
gridded 0.22447963798069204
Topic 23:
dogmas 0.8110790918659693
kku 0.6555487689949174
w7zgyke 0.2255854581886749
legitimizing 0.22850091721818022
odb 0.3540420168715243
gnarly 0.11880703827687594
sund

145 0.38401823688355746
1d9 0.9684088672783833
pink 0.28906638637742427
0t 0.9104569787362049
34u 0.7939950840419728
2di 0.9764705699705306
75u 0.9387874431414139
1t 0.8863738357948785
bglr 0.9574000122425539
gigerment 1.0
3t 0.8901108469229265
wimped 0.2250320892329194
2tm 0.9828901884496244
0d 0.8383986203808766
bvfp 1.0
Topic 39:
mr9rm 1.0
focal 0.8913210951847373
chibi 0.9611598301935576
ealigernuk 0.5967268631481808
foci 0.8059270990738986
fjz969s 0.9841470938908389
glasses 0.9177399447556972
raytracing 0.7030444591427106
reroute 0.9709811930871081
tahir 0.6102262737327376
edw 0.37882763301486144
bql6s3 0.37477746894001485
catchup 0.18026017077681503
diciples 0.5146178106955288
strait 0.17825188300585998
rerun 0.9627260015804954
sabellius 0.620658458660415
carbujector 0.6641569122178429
najznb8 0.22738362148565083
allegro 0.730433743137561
Topic 40:
nesbitt 0.9896141260474495
ydoh 0.5397061499338476
braces 0.2986267760192591
premepted 0.10665052597604688
oftimes 0.0920535173566794

In [ ]:
######## DUC dataset

In [26]:
import os
def get_filenames(folder):

    filenames= os.listdir(folder)
    return filenames

path = "Downloads/DUC2001/"
filenames = get_filenames(path)

def get_text(content):
    #print(content)
    doc_text = []
    done = False
    for i in range(len(content)):
        #line = line.strip() # skip the empty line
        line = content[i].lstrip()
        #line = line.replace('\n','')
        
        if line == '<TEXT>\n':
            
            for j in range(i+1,len(content)):
                if content[j] == '</TEXT>\n':
                    done == True
                    break
                doc_text.append(content[j].strip())
        if done:
            break
    #print(doc_text)
    return doc_text
 
fileCon = ''
i = 0
documents_duc = []
exclude = ['annotations.txt','.DS_Store','kartest','Summaries','notes.txt']
for filename in filenames:
    if filename in exclude :
        continue
    #filename = 'FBIS-41815'
    fd = open(path +'/'+ filename, "r+")
           
    fileCon = fd.readlines()
    fd.close()
    #print(fileCon)
    text = get_text(fileCon)
    text = ''.join(text)
    documents_duc.append(text)
    
    

In [88]:
def display_topics_DUC(model, feature_names, no_top_words):
    for i in range(model.components_.shape[0]):
        print('\nTopic %d:' % (i))
        topic = model.components_[i]
        result = dict()
        new_topic = topic.argsort()[:-no_top_words - 1:-1]
        for j in new_topic:
            result[feature_names[j]] = topic[j] / np.sum(model.components_, axis=0)[j]
            print(feature_names[j], topic[j] / np.sum(model.components_, axis=0)[j])
        es.index(index='topic_duc', doc_type='topic_duc',id=i,body={
            'topic_id': i,
            'top_words': result
            })

In [89]:
###print top 20 words for the topics
i = 0
while i < 3:
    if i == 0:
        no_topics = 10
    elif i == 1:
        no_topics = 20
    elif i == 2:
        no_topics = 50
    tf,tfidf_feature_names = get_tf_vector(documents_duc)
        
    lda = LatentDirichletAllocation(n_topics=no_topics).fit(tf)
    print("------- Top 20 words for all docs for K=",no_topics)
    r = display_topics_DUC(lda,tfidf_feature_names,20)
    i+=1

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)


------- Top 20 words for all docs for K= 10

Topic 0:
the 0.0007488803311088843
mahgoub 0.7749116078933972
sendero 0.550498804546422
of 0.0005560751769612725
ge 0.6909637966173633
cfm56 0.6733112199057969
and 0.0006688204587629379
el 0.11267506489255825
egyptian 0.5451329115715285
funeral 0.4240944779916868
slums 0.6108560697400278
tablet 0.6026638133035035
to 0.0005134939265234924
mubarak 0.6529907679952524
extremists 0.6464211070130363
egypt 0.6473998660856889
ahram 0.6470239048671236
said 0.001614459919812858
737 0.6244687647874733
in 0.00048711394669926196

Topic 1:
and 3.297228859080159e-05
refinancing 0.04122309700702546
the 1.0934141829219188e-05
johnson 0.0012353033166700345
acrowd 0.06842636203541022
ordinarily 0.06834782036426762
achieving 0.06573975034763795
surviving 0.06574813657288471
of 2.3339838651846846e-05
cayman 0.06778270576609427
iaaf 0.02271884625219408
attorneyand 0.06788277957489025
it 9.863051749459067e-05
6bn 0.02611324465519447
shovels 0.04864858743068485
enc

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)


------- Top 20 words for all docs for K= 20

Topic 0:
the 3.6243558166769544e-05
to 5.346058817254608e-05
said 0.0001670874780059196
in 4.9673755791472894e-05
he 0.0001816237289653749
of 3.484321369122676e-05
and 4.5603925211879275e-05
was 0.00011922246704504931
it 9.544277411831246e-05
with 0.0001287085488463113
his 0.00023143852731641792
on 9.0296495421036e-05
from 0.00013069052141072163
johnson 0.0010900786375004918
at 0.00013056715115961366
as 0.00010623783099106342
is 6.279734100907656e-05
for 6.93740721471128e-05
by 0.00010142414218159362
be 0.00010619026694300856

Topic 1:
the 2.2648281886811315e-05
in 4.1673886800054856e-05
to 3.672711186730391e-05
and 4.2257729571647845e-05
of 2.8698665630704532e-05
said 0.00010429052718664081
was 0.00011509809949942038
were 0.00022872292889516448
at 0.00013133579673319158
it 8.153712075761665e-05
one 0.00021832209595999227
from 0.00011635742102397917
forest 0.0008406596808768609
that 4.3452771776746525e-05
is 5.8259558872322206e-05
but 0.0001


Topic 17:
the 6.704065516443821e-05
in 0.00014412115528853261
to 0.00010108837582752022
of 8.233264105287326e-05
said 0.00027910464333965327
and 9.023729041887914e-05
that 0.00011541955558446873
it 0.00018186680844502095
was 0.00019217744209190185
is 0.00012554251572108717
on 0.0001567429616457716
for 0.00011521365425470839
he 0.0001470585610137388
but 0.00019861220386236034
were 0.0002844938039421002
his 0.0002838988414897919
with 0.00015427337544860067
an 0.00020368159974970567
by 0.0001460073277648346
as 0.0001371961489580562

Topic 18:
the 3.241004619278254e-05
to 4.883795523005663e-05
of 4.039458374336251e-05
in 4.7929147435359414e-05
that 7.292158888963e-05
and 3.341896383483079e-05
said 0.00010008198195898019
on 9.91444066017383e-05
was 0.00011667380209303942
is 7.381018127965889e-05
it 9.392281152219944e-05
be 0.0001239601057548376
by 0.00011655943491807605
for 7.259855681561468e-05
forest 0.0008838466349278335
have 0.00012383024559062055
fire 0.00042615128675629557
aliens 0.0

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)


------- Top 20 words for all docs for K= 50

Topic 0:
wasessential 0.013658348894755108
cairobridges 0.019422829874963413
beat 0.004542341818360307
willresuscitate 0.01861077390798066
reference 0.013223323540218563
browbeats 0.01863954912912324
franciscoruiz 0.018502404119853762
sobadly 0.018198386415680216
lobbyist 0.008196237376933084
yvonnejohnson 0.018360977724028938
willshortchange 0.01837394334749794
nato 0.010993253913003783
approached 0.007041126352094096
530million 0.018730641090397838
tampering 0.012937719343326059
pressler 0.008808923827758943
treesbefore 0.01837494113419677
golobsaid 0.014958374106871088
conquerors 0.01844429932885372
aflip 0.018551059431563835

Topic 1:
tornado 0.49456887047419523
homes 0.3479718627392741
the 0.0005059132797232753
twister 0.6617445707370153
acres 0.07059633110685153
and 0.0011177836775504494
destroyed 0.16109898723161245
in 0.0009724962182624231
peavy 0.628848949734444
injured 0.13384236160941607
gila 0.6142766865816566
said 0.002884373031


Topic 15:
52 0.2942254336692342
sawyer 0.6467781412426118
bomber 0.4253580804542682
lt 0.19952127267609035
peck 0.5496899164548793
1st 0.4865904607089634
the 0.00019790433316304242
bailey 0.2578597741435901
debruzzi 0.48483337804997373
fly 0.1443809803172407
wurtsmith 0.3883622297167073
1b 0.3894764931233253
1bs 0.3899833182793674
forcebase 0.3841020257754649
airman 0.3853849656232709
minn 0.3870371916372019
kroeger 0.38302903885212414
sac 0.38388808717451245
marquette 0.38202072679119004
mccarrick 0.3846961708209814

Topic 16:
the 6.485026706125693e-06
in 1.81483431825398e-05
tb 0.0015428013180437327
of 1.1183549187863896e-05
cases 0.0009293435603384757
an 8.251814314142903e-05
and 1.4839180451364781e-05
for 3.8272291338100545e-05
tuberculosis 0.001019638058479102
that 2.4394098910167187e-05
ruben 0.019126509655717605
title 0.01513770896833547
measuring 0.00769275033621901
trigger 0.005287158485264727
aids 0.0014899599328634218
1987 0.0011021258332575938
disease 0.0004333087899903299

said 4.3474810043993895e-05
danny 0.012930406431284725
thelebanese 0.019008058174847648
his 0.0001046948183846904
assist 0.00866963583974447
hadindicated 0.018642873053530244
this 8.726752705341646e-05
fujimorigovernment 0.018442244681078444
knowntheir 0.01823841940449626

Topic 31:
colosio 0.5762184972456499
94 0.4599926857369806
mexican 0.09187344339738403
mar 0.44013322021396206
gmt 0.37368295479253183
prensa 0.3722523679042012
menendez 0.3729369459111826
hamburg 0.3749754048060973
arena 0.37124514916691875
condolences 0.3745975924762767
dpa 0.36884750447319054
venezuelan 0.373951040911454
latina 0.36806001677501127
sassassination 0.30566633801870446
donaldo 0.29551012308807995
counterpart 0.29182288124229233
express 0.20146720094339857
disclosed 0.16555450012392678
pri 0.17108629096672096
spanish 0.09534302381580344

Topic 32:
_tornadoes 0.3179060119501461
_the 0.21387393079684738
orcentral 0.2493552448513498
26miles 0.24774088551478138
wheretornadoes 0.24833579166775757
pathscan 0

academy 0.006935252127848811
punished 0.018456839971293007
waskilled 0.018298682025402677
thatformally 0.018589361524801777
pushes 0.018466748958056473
conceived 0.01876172915863599
oneparticipant 0.012960035973328888
diverts 0.018289504524314795
shah 0.018399640617277575
ibelieve 0.018496189962706442
mythified 0.01283232724458998
998 0.014832702149103623
aviation 0.002263035952487504
takechances 0.01863888156356872
criticism 0.006493633092884021

Topic 46:
in 1.6818504204980522e-05
and 1.6489617534947424e-05
to 1.3962382710742057e-05
said 4.8729518516074614e-05
the 5.36039170346829e-06
forest 0.0005073856699273283
was 5.5267826678988974e-05
of 1.105184919339802e-05
miss 0.0015491072542390563
weir 0.01588200687347863
taylor 0.0009683774839251995
acres 0.0008134360202717316
pneumonia 0.002143696355435168
reformwelfare 0.018639614934651005
apress 0.018560236004484674
firstterms 0.013132747785376186
antigua 0.01890380226722832
listen 0.018489456634081438
licenses 0.013029909925849787
mcgo

In [90]:
def display_topics_DUC_NMF(model, feature_names, no_top_words):
    for i in range(model.components_.shape[0]):
        print('\nTopic %d:' % (i))
        topic = model.components_[i]
        result = dict()
        new_topic = topic.argsort()[:-no_top_words - 1:-1]
        for j in new_topic:
            result[feature_names[j]] = topic[j] / np.sum(model.components_, axis=0)[j]
            print(feature_names[j], topic[j] / np.sum(model.components_, axis=0)[j])
        

In [93]:
# NMF is able to use tf-idf
tfidf_vectorizer = TfidfVectorizer(stop_words='english')
tfidf_duc = tfidf_vectorizer.fit_transform(documents_duc)
tfidf_feature_names = tfidf_vectorizer.get_feature_names()

In [95]:
# Run NMF
i = 0
while i < 3:
    if i == 0:
        no_topics = 10
    elif i == 1:
        no_topics = 20
    elif i == 2:
        no_topics = 50
    
    nmf = NMF(n_components=no_topics).fit(tfidf_duc)
    print("------- NMF Top 20 words for K=",no_topics)
    no_top_words = 20
    display_topics_DUC_NMF(nmf, tfidf_feature_names, no_top_words)
    i += 1
    

------- NMF Top 20 words for K= 10

Topic 0:
census 1.0
aliens 1.0
illegal 0.9738810145212359
seats 1.0
count 0.9662989309427589
bureau 0.9869252451865437
house 0.6080626727567319
senate 0.8607717646822685
states 0.5948928694458238
counting 0.9723176559664846
immigration 1.0
said 0.10371135392762176
california 0.5558025055490116
counted 0.9998913622491111
constitution 0.828529455918082
rep 0.8140554639081051
congress 0.47108508844459296
amendment 0.6755691571960936
county 0.5605929116742778
population 0.6751774561935433

Topic 1:
oil 0.9825964306331525
exxon 1.0
spill 1.0
valdez 1.0
said 0.10527983052037423
alaska 0.9414218066333758
cleanup 1.0
tanker 1.0
sound 0.9151799868755259
guard 0.69721070299485
ship 0.9220251327397005
coast 0.5123611953799541
miles 0.3026536208608315
hazelwood 1.0
prince 0.9956194608854311
million 0.2103861520403735
reef 1.0
crude 0.978107939183661
gallons 0.964091879716991
vessel 0.865546866288926

Topic 2:
hurricane 1.0
hurricanes 1.0
sheets 1.0
storm 0.97254

contained 0.8743814582473771
rain 0.7621633982257182
burning 0.8747391911938722
burn 0.9001328595657678

Topic 10:
nafta 1.0
mr 0.22432142305157995
trade 0.5754654810760114
pact 0.9892795280012816
clinton 0.5114490027156545
congressman 0.8924232230813289
mexico 0.3833993424223551
daley 0.6286968113422532
president 0.18833680293297902
perot 1.0
vote 0.3015565772713352
agreement 0.44845254308853505
opposition 0.721963734586554
anti 0.4738444433857503
house 0.09890826811925887
labour 0.841229250064856
administration 0.35827543684839647
pro 0.682767286911449
jobs 0.47437671528743064
congressmen 0.9961127257174875

Topic 11:
slovenia 0.9933718935121029
yugoslavia 0.9819440845642675
slovene 0.9572067193704233
serbia 0.9984832166299182
croatia 0.9916890671107659
slovenian 0.9696340444575805
yugoslav 0.9987810598549209
republic 0.7761988826840629
republics 0.9882927640619021
slovenes 0.983263381101336
serbian 0.999401700848916
war 0.2985282146980745
federal 0.14861748356855844
independence 0.8

st 0.6264723282148562
hospitalized 0.7711906357819822
bacterial 0.9423523072323053
john 0.3143763805041051
sam 0.9079349420728775
condition 0.24958336416604623
elizabeth 0.720836930794114
chen 1.0
health 0.18574106659020737
weeks 0.2614921790811283
statement 0.22307913446870292
publicist 0.9984504483739362
addiction 0.7225443418594891

Topic 9:
welfare 0.9878366935659965
reform 0.6200398805599547
governors 0.7641002998974408
benefits 0.5837188055904405
recipients 0.8485191028019905
work 0.1763693021134126
families 0.5380793846938504
programs 0.4654308580855781
president 0.1060228578252554
clinton 0.16312203030178576
poverty 0.1294131478095566
plan 0.11803819938218603
spending 0.40629700732995494
training 0.13562390151796522
congress 0.08142063934784946
children 0.1945364840305909
dependency 0.8381606748958719
programmes 0.49297553704655994
democrats 0.20006993926861114
downey 0.6745002006619392

Topic 10:
nafta 1.0
pact 0.9604869093161164
trade 0.41692968699692806
clinton 0.30122873264

exercise 0.7721409597358749

Topic 26:
cellrule 1.0
tablecell 1.0
chj 1.0
cvj 1.0
rowrule 0.9953709221015528
tablerow 0.9959289753541337
samuelson 0.9464017587232418
kristiansen 0.946401758723242
marathon 0.06918623623991649
mekonnen 0.946401758723242
ethiopia 0.28381316344304786
beaten 0.283585279754589
ikangaa 0.32988529798434413
ethiopians 0.2934649169485571
boston 0.05960509121032545
world 0.017687957473359918
won 0.0359851256598203
dinsamo 0.946401758723242
abebe 0.946401758723242
cup 0.6000060631384029

Topic 27:
thomas 0.9349142227240166
judge 0.5466658911051824
mr 0.09818800288814625
clarence 0.8717317892595267
nuns 0.987232611953145
nomination 0.9414697663748136
law 0.26118188760235833
circuit 0.9145141893556917
danforth 0.9916215183114512
senate 0.1733317757795634
chairman 0.26548337727245985
man 0.20739374109856276
sen 0.3231492889317423
court 0.1882944448507342
left 0.2084183001379992
people 0.06633074300229089
affirmative 0.9973572162603064
eeoc 0.9461356810971344
discrimi

rainfall 0.2927711123120773
hills 0.5429605328985107
map 0.516621634852055
drought 0.07094361382426433
drive 0.29894607035159715
chaparral 0.9753414408525856

Topic 45:
chong 1.0
prosecution 0.7833752768145695
paek 1.0
prosecutor 0.8209202227406279
kim 0.8239856790956591
joint 0.6516877017687224
1979 0.32828366161502515
military 0.11683600711599165
hui 1.0
lawcommander 1.0
hwa 1.0
team 0.3243244714794791
dec 0.3944429547372578
martial 0.9427882593062568
theassassination 0.6940069054261608
evidence 0.26221696169825653
office 0.12802465168152924
treason 1.0
accomplice 1.0
chon 1.0

Topic 46:
jet 0.5838842347432998
navy 0.8315143289162094
crash 0.14053286003476984
aircraft 0.235466869973638
said 0.028413285639684985
pensacola 0.99008979671779
naval 0.946639737490789
fighter 0.2097992875697791
kasper 0.9900897967177898
training 0.2727913518737797
carrier 0.9171167497898414
lexington 0.8683034258353524
coast 0.07842592346549548
deck 0.6321005010832147
guard 0.06812889387850693
notification 

In [99]:
# Run LDA
i = 0
while i < 3:
    if i == 0:
        no_topics = 10
    elif i == 1:
        no_topics = 20
    elif i == 2:
        no_topics = 50
    
    for index in range(len(documents_duc)):
        
        tf,tfidf_feature_names = get_tf_vector([documents_duc[index]])
        
        if tf is not None:
                lda = LatentDirichletAllocation(n_topics=no_topics).fit(tf)

                a=lda.transform(tf)
                result = OrderedDict()
                
                new_topic=a[0].argsort()[:-5 - 1:-1]
                for i in range(len(new_topic)):
                    result[str(new_topic[i])] = a[0][new_topic[i]]
                
                print("------- Top 20 words for K=",no_topics)
                no_top_words = 20
                #result_topics = get_topics(lda, tf_feature_names, 5)
                
                
                es.index(index='index_duc', doc_type='duc',id=index,body={
                'doc_id': index+1,
                'doc_text': documents_duc[index],
                'doc_topics': result
                })
        else:
                result[str(-1)] = 0.0
                es.index(index='index_duc', doc_type='duc',id=index,body={
                'doc_id': index+1,
                'doc_text': documents_duc[index],
                "doc_topics": result
                })
    i += 1
    

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

...

/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online

------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10
------- Top 20 words for K= 10


/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:536: DeprecationWarning: The default value for 'learning_method' will be changed from 'online' to 'batch' in the release 0.20. This warning was introduced in 0.18.
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/usr/local/Cellar/python3/3.6.4_2/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/decomposition/online